# model TPH

In [4]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from datetime import timedelta
import re
from dateutil.parser import parse
import string
import warnings
warnings.filterwarnings('ignore')
import plotly.graph_objects as go
import missingno as msno
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import scipy
import researchpy as rp
from matplotlib.offsetbox import AnchoredText
import pacmap
from sklearn.compose import ColumnTransformer
from sklearn.cluster import KMeans
from sklearn.pipeline import Pipeline
import plotly.express as px
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from imblearn.over_sampling import RandomOverSampler
from sklearn.model_selection import train_test_split 
# Import Halving Grid Search
from sklearn.experimental import enable_halving_search_cv 
from sklearn.model_selection import HalvingGridSearchCV
import xgboost as xgb
from scipy.stats import kurtosis,skew
from numpy import mean,sqrt,square
from scipy.fftpack import fft, fftfreq
from sklearn.metrics import mean_squared_error
sns.set_style("darkgrid")
pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 100

In [1]:
# Función que filtra tags por alta correlación
def corrkill(dataframe, features, corr_cut=0.8):

    df = dataframe[features]
    dfcorr = pd.DataFrame(np.triu(df.corr()), columns=df.columns, index=df.columns)
    dfcorr = dfcorr.stack().reset_index()
    dfcorr.columns = ['Feat1','Feat2','Val']
    dfcorr = dfcorr[~dfcorr['Val'].isin([0,1])]
    dfcorr = dfcorr[dfcorr['Val'].abs()>corr_cut]
    dfcorr["Val"]=dfcorr["Val"].abs()
    
    return list(dfcorr['Feat2']), dfcorr.sort_values(by="Val",ascending=False)

In [2]:
variables_interes=['pyrite law', 'chalcopyrite law',
       'chalcocite law', 'covelin law', 'crusher index', 'sag power index',
       'ball work index', 'bornite law','charge cell', 'TPH','water', 'speed','HH TPH', 'granulometry', 'Edad','loss of TPH']
variables_interes

['pyrite law',
 'chalcopyrite law',
 'chalcocite law',
 'covelin law',
 'crusher index',
 'sag power index',
 'ball work index',
 'bornite law',
 'charge cell',
 'TPH',
 'water',
 'speed',
 'HH TPH',
 'granulometry',
 'Edad',
 'loss of TPH']

In [ ]:
# read df full csv
df_full=pd.read_csv('../../data/consolidated data/df_full_01November2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')[variables_interes]["2020":"2021"]
df_full

In [ ]:
df_corr = df_full.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))
top_corr=corr_tph[corr_tph.TPH>=0]
top_corr

# Feature Engineering

In [ ]:
def feature_engineering(df):
      
    targets = ["TPH","Edad","loss of TPH","HH TPH"]
    df_vars = df.copy()
    column_inicial=df_vars.columns

    for column in df_vars:
    
        if (column not in targets):

            ## 10 min
            df_vars[f"skew_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:skew(x))
            df_vars[f"kurt_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: np.nanvar(x))

            # 5 min
            df_vars[f"mean_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: np.nanvar(x))

            # 3 min
            df_vars[f"skew_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:skew(x))
            df_vars[f"kurt_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: np.nanvar(x))

            # Fourier
            #L=10
            #df_vars[f"fourier_{L}_max_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmax(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_min_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmin(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_mean_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmean(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_sum_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nansum(abs(fft(list(x))[1:int(L/2)]/(L/2))))
#
            #L=5
            #df_vars[f"fourier_{L}_max_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmax(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_min_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmin(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_mean_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmean(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_sum_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nansum(abs(fft(list(x))[1:int(L/2)]/(L/2))))


    for column in column_inicial:
        if (column not in targets):
            # lags  
            df_vars[f"{column}_(t-1)"] = df_vars[column].shift(1)
            df_vars[f'{column}_(t-2)'] = df_vars[column].shift(2)
            df_vars[f'{column}_(t-3)'] = df_vars[column].shift(3)
            df_vars[f'{column}_(t-4)'] = df_vars[column].shift(4)
            df_vars[f'{column}_(t-5)'] = df_vars[column].shift(5)
           
    
    return df_vars
   

In [ ]:
df_features=feature_engineering(df_full)

In [ ]:
# Se guarda en csv
df_features.to_csv('../../data/consolidated data/df_features_'+pd.to_datetime('today').strftime('%d%B%Y')+'.csv', index=True)

In [5]:
# read df full csv
df_features=pd.read_csv('../../data/consolidated data/df_features_05November2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')["2020":"2021"]
df_features["TPH"]=df_features["TPH"].shift(-5)
df_features["loss of TPH"]=df_features["loss of TPH"].shift(-5)
df_features.dropna(inplace=True)
df_features.sort_index(inplace=True)
df_features.shape

(796472, 340)

# Correlación entre variables

In [ ]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(df_features,df_features.columns)

In [ ]:
# Tags altamente correlacionados
table_cor

In [ ]:
df_corr = df_features.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))


In [ ]:
top_corr=corr_tph[corr_tph.TPH>=0.15]
top_corr

# Equilibrio de eventos de perdidas de TPH

In [6]:
# Generación de targets ficticio y features
target=df_features["2020":"2021-11"]["loss of TPH"].copy()
features=df_features["2020":"2021-11"].drop(columns=["loss of TPH"])

# Generación conjunto de train y test 
Xtrain, Xtest, Ytrain, Ytest = train_test_split(
    features, target, test_size=0.33, 
    random_state=42
)

# Sobremuestreo: Aumentar numero de datos de la clase minoritaria (perdida de TPH)
# ROS(Duplica clases):
ros=RandomOverSampler(random_state=0) # Random_state=0

# ROS:
Xtrain, Ytrain=ros.fit_resample(Xtrain,Ytrain)

In [7]:
Color_loss=Ytest
Color_loss=Color_loss.astype(str)

In [8]:
# Ytest reg
Ytest=Xtest["TPH"]
Xtest=Xtest.drop(columns=["TPH"])

In [9]:
# Ytrain reg
Ytrain=Xtrain["TPH"]
Xtrain=Xtrain.drop(columns=["TPH"])

# Feature selection

In [ ]:
# Generación de targets ficticio y features
#target=df_features["2020":"2021-11"]["TPH"].copy()
#features=df_features["2020":"2021-11"].drop(columns=["loss of TPH","TPH"])
#
## Generación conjunto de train y test 
#Xtrain, Xtest, Ytrain, Ytest = train_test_split(
#    features, target, test_size=0.33, 
#    random_state=42
#)

In [ ]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        Xtrain.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [ ]:
pipe.fit(Xtrain, Ytrain)

In [ ]:
Ypred= pipe.predict(Xtest)

# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

In [ ]:
# test 2021
test_time_serie=df_features["2021-12"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)
#test_time_serie["TPH predict"]=test_time_serie["TPH predict"].shift(5)
test_time_serie.dropna(inplace=True)

# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))

In [ ]:
df_importance=pd.DataFrame({"tag":Xtrain.columns,"importance":pipe["clf"].feature_importances_}).sort_values(by="importance",ascending=False).reset_index(drop=True)
df_importance.head()

In [ ]:
pd.options.plotting.backend = "plotly"
fig=df_importance["importance"].plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [ ]:
# Plot
fig = go.Figure([go.Bar(x=df_importance["tag"], y=df_importance["importance"])])
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [ ]:
xgboost_fs=df_importance[:100].tag.to_list()
xgboost_fs

In [ ]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(Xtrain,xgboost_fs,corr_cut=0.9)

In [ ]:
# Tags altamente correlacionados
table_cor

In [ ]:
tag_select = [i for i in xgboost_fs if i not in collinearity]
tag_select

In [ ]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [ ]:
pipe.fit(Xtrain, Ytrain)

In [ ]:
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

# GridSearch

In [ ]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        #features.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
        #("Selection", SelectPercentile(f_classif, percentile=10)),
        #("PCA",PCA(n_components=150 )), #0.08
     ("reg", xgb.XGBRegressor(seed=1,eval_metric='rmse'))
    ]
)


param_grid_reg = {'reg__learning_rate': list(np.linspace(0.001,1,10)), # Boosting learning rate
                  'reg__gamma':list(np.linspace(0.0001,50,5)), # Minimum loss reduction required to make a further partition on a leaf node of the tree.
                  #'reg__max_depth':[5,10,12,15,20], # Maximum tree depth for base learners.
                  #'reg__min_child_weight':[10,5,1,2,3], # Minimum sum of instance weight(hessian) needed in a child.
                  #'reg__colsample_bytree':[0.5,0.8,1], # Subsample ratio of columns when constructing each tree.
                  'reg__n_estimators': [100,200,300], # Number of gradient boosted trees.   
                  #'reg__reg_alpha': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
              #'reg__reg_lambda': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
               #'Selection__percentile': [10,20,30,50,70,80,100]              
                 } 

# Clasificación
gs_reg = HalvingGridSearchCV(pipe, param_grid_reg, scoring='neg_mean_absolute_error',cv=5,refit=True,
                             verbose=10,
                             aggressive_elimination=True
                            )

# Fit
gs_reg.fit(Xtrain, Ytrain)

In [ ]:
gs_reg.best_score_

In [ ]:
gs_reg.best_params_

In [ ]:
Ypred= gs_reg.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

# Train model

In [10]:
tag_select=['min_water_5',
 'HH TPH',
 'rms_speed_10',
 'rms_sag power index_10',
 'max_charge cell_10',
 'min_granulometry_10',
 'chalcocite law_(t-3)',
 'min_pyrite law_5',
 'max_bornite law_10',
 'Edad',
 'mean_crusher index_3',
 'var_water_10',
 'var_covelin law_5',
 'var_charge cell_10',
 'min_ball work index_10',
 'min_chalcopyrite law_10',
 'covelin law_(t-4)',
 'var_crusher index_3',
 'var_bornite law_10',
 'var_speed_10',
 'var_chalcocite law_3',
 'var_water_5',
 'var_sag power index_3',
 'var_ball work index_3']

In [11]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse',gamma= 0.0001, learning_rate= 0.334, n_estimators= 300
     
     ))
    ]
)
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['min_water_5', 'HH TPH',
                                                   'rms_speed_10',
                                                   'rms_sag power index_10',
                                                   'max_charge cell_10',
                                                   'min_granulometry_10',
                                                   'chalcocite law_(t-3)',
                                                   'min_pyrite law_5',
                                                   'max_bornite law_10', 'Edad',
                                                   'mean_crusher index_3',
                                                   'var_water_10',
                                                   'var_covelin law_5',
                                                   'var_charge cell_10',
      

In [31]:
from sklearn.metrics import mean_absolute_percentage_error

In [33]:
mean_absolute_percentage_error(Ytest, Ypred)*100

2.2275390026575117

In [34]:
# test 2020
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False),'\n','MAPE :',mean_absolute_percentage_error(Ytest, Ypred)*100)

R2:  0.9051879089713314 
 RMSE:  139.00180710875935 
 MAPE : 2.2275390026575117


In [18]:
# Create traces
fig = px.scatter(x=Ypred[:10000], y=Ytest[:10000],trendline="ols",trendline_color_override="red",labels={'y': 'Test',"x":"Predict"},color=Color_loss[:10000])
fig.update_layout(height=500, width=1200, title_text="Scatter predict/test")
fig.show()

In [26]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(y=Ypred[:1000], 
                    mode='lines',name="predict"
                    ))

fig.add_trace(go.Scatter(y=Ytest[:1000],
                    mode='lines',name="Test",#marker=dict(color=list(Color_loss[:1000]))
                    ))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict")
fig.show()

# Simulation time series predict

In [27]:
# test 2021
test_time_serie=df_features["2021-12"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)
#test_time_serie["TPH predict"]=test_time_serie["TPH predict"].shift(5)
test_time_serie.dropna(inplace=True)

# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))

R2:  0.7599387766172159 
 RMSE:  173.08868942734577


In [28]:
data=test_time_serie
data.head()

pyrite law  chalcopyrite law  chalcocite law  \
Timestamp                                                           
2021-12-01 00:00:00        2.04               1.0            0.29   
2021-12-01 00:01:00        2.04               1.0            0.29   
2021-12-01 00:02:00        2.04               1.0            0.29   
2021-12-01 00:03:00        2.04               1.0            0.29   
2021-12-01 00:04:00        2.04               1.0            0.29   

                     covelin law  crusher index  sag power index  \
Timestamp                                                          
2021-12-01 00:00:00         0.02        19.9309           118.08   
2021-12-01 00:01:00         0.02        19.9309           118.08   
2021-12-01 00:02:00         0.02        19.9309           118.08   
2021-12-01 00:03:00         0.02        19.9309           118.08   
2021-12-01 00:04:00         0.02        19.9309           118.08   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2021-12-01 00:00:00          16.3835         0.01   768.741664  3768.121499   
2021-12-01 00:01:00          16.3835         0.01   769.288545  3785.106874   
2021-12-01 00:02:00          16.3835         0.01   769.324759  3818.192803   
2021-12-01 00:03:00          16.3835         0.01   771.590130  3729.452391   
2021-12-01 00:04:00          16.3835         0.01   772.882214  3750.067451   

                           water     speed  HH TPH  granulometry  Edad  \
Timestamp                                                                
2021-12-01 00:00:00  2036.974410  9.295474  4200.0     53.602944   2.0   
2021-12-01 00:01:00  2040.755290  9.294131  4200.0     53.646366   2.0   
2021-12-01 00:02:00  2039.094777  9.294869  4200.0     53.563687   2.0   
2021-12-01 00:03:00  2037.114180  9.298192  4200.0     53.712367   2.0   
2021-12-01 00:04:00  2040.755205  9.297221  4200.0     53.944855   2.0   

                     loss of TPH  skew_pyrite law_10  kurt_pyrite law_10  \
Timestamp                                                                  
2021-12-01 00:00:00          1.0       -2.666667e+00            5.111111   
2021-12-01 00:01:00          1.0       -1.500000e+00            0.250000   
2021-12-01 00:02:00          1.0       -8.728716e-01           -1.238095   
2021-12-01 00:03:00          1.0       -4.082483e-01           -1.833333   
2021-12-01 00:04:00          1.0        7.436229e-15           -2.000000   

                     mean_pyrite law_10  max_pyrite law_10  sum_pyrite law_10  \
Timestamp                                                                       
2021-12-01 00:00:00               2.202               2.22              22.02   
2021-12-01 00:01:00               2.184               2.22              21.84   
2021-12-01 00:02:00               2.166               2.22              21.66   
2021-12-01 00:03:00               2.148               2.22              21.48   
2021-12-01 00:04:00               2.130               2.22              21.30   

                     min_pyrite law_10  rms_pyrite law_10  var_pyrite law_10  \
Timestamp                                                                      
2021-12-01 00:00:00               2.04           2.202662           0.002916   
2021-12-01 00:01:00               2.04           2.185186           0.005184   
2021-12-01 00:02:00               2.04           2.167570           0.006804   
2021-12-01 00:03:00               2.04           2.149809           0.007776   
2021-12-01 00:04:00               2.04           2.131901           0.008100   

                     mean_pyrite law_5  max_pyrite law_5  sum_pyrite law_5  \
Timestamp                                                                    
2021-12-01 00:00:00              2.184              2.22             10.92   
2021-12-01 00:01:00              2.148              2.22             10.74   
2021-12-01 00

In [35]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

#fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
#                    mode='lines',
#                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()

In [36]:
fig.write_html("file.html")